In [12]:
import numpy as np
import math
import random
import os

from path import Path

import plotly.graph_objects as go
import plotly.express as px

In [13]:
# ici on recupère le path a l'aide de la bibli path
# cette operation serais egalement réalisable de manière plus
# traditionel 

path = Path("ModelNet10")
print(path)

ModelNet10


In [21]:
# Un fichier off comporte plusieurs infomation importante pour crée le mesh et representé l'objets
# en 3d. On récupere ici les faces et les vertices de chaque mesh (les vertices sont les sommets)
# puis on les stock en deux variables distincte faces et verts. Lire et stocké ces informations
# reviens a lire et stocké un ficher off (tout simplement)
def read_off(file):
    if 'OFF' != file.readline().strip():
        raise('Not a valid OFF header')
    n_verts, n_faces, __ = tuple([int(s) for s in file.readline().strip().split(' ')])
    verts = [[float(s) for s in file.readline().strip().split(' ')] for i_vert in range(n_verts)]
    faces = [[int(s) for s in file.readline().strip().split(' ')][1:] for i_face in range(n_faces)]
    return verts, faces


# ici on spécifie un path vers un objets en particulier, en l'occurence on ouvre un model de sofa 
with open(path/"ModelNet10/sofa/train/sofa_0021.off", 'r') as f:
  verts, faces = read_off(f)


# Ici on va crée de novelle variables sous la formes de array dans le but de crée un fonction de display
# propres qui nous permettras de visualiser l'objets que nous avons charger grace a plotly 
i,j,k = np.array(faces).T
x,y,z = np.array(verts).T
len(x)

26476

In [23]:
# Cette fonctionne permet des crée un animation de l'objets 3d et de visualiser le mesh dans un déplacement
# cours (rotation sur l'axe z )
def visualize_rotate(data):
    x_eye, y_eye, z_eye = 1.25, 1.25, 0.8
    frames=[]

    def rotate_z(x, y, z, theta):
        w = x+1j*y
        return np.real(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w), z

    for t in np.arange(0, 10.26, 0.1):
        xe, ye, ze = rotate_z(x_eye, y_eye, z_eye, -t)
        frames.append(dict(layout=dict(scene=dict(camera=dict(eye=dict(x=xe, y=ye, z=ze))))))
    fig = go.Figure(data=data,
                    layout=go.Layout(
                        updatemenus=[dict(type='buttons',
                                    showactive=False,
                                    y=1,
                                    x=0.8,
                                    xanchor='left',
                                    yanchor='bottom',
                                    pad=dict(t=45, r=10),
                                    buttons=[dict(label='Play',
                                                    method='animate',
                                                    args=[None, dict(frame=dict(duration=50, redraw=True),
                                                                    transition=dict(duration=0),
                                                                    fromcurrent=True,
                                                                    mode='immediate'
                                                                    )]
                                                    )
                                            ]
                                    )
                                ]
                    ),
                    frames=frames
            )

    return fig

visualize_rotate([go.Mesh3d(x=x, y=y, z=z, color='lightblue', opacity=0.40, i=i,j=j,k=k)]).show()


In [40]:
# ici plutot que de visualisé le mesh on ne display que les point 
# on remarque quand ces derneirs se positionne essentielement sur les 
# bord et ou les angle mais pas sur les surface plate 
# cela va posé des probleme a pointnet il faut donc changer la
# repartition des point 

visualize_rotate([go.Scatter3d(x=x, y=y,z=z, mode='markers',
                               marker = dict(size = 1, opacity = 0.4))]).show()

In [41]:
# ceci es un nouvelle fonction pour display le nuage de point plus "proprement"

def pcshow(xs,ys,zs):
    data=[go.Scatter3d(x=xs, y=ys, z=zs,
                                   mode='markers')]
    fig = visualize_rotate(data)
    fig.update_traces(marker=dict(size=2,
                      line=dict(width=2,
                      color='DarkSlateGrey')),
                      selector=dict(mode='markers'))
    fig.show()
    

pcshow(x,y,z)